# Exploratory Data Analysis  

## Summary

### Import libraries and data

### Clean data, engineer extra features
1. Recast date columns as type date time
2. Add columns for hour of day, day of week, day of month, month of year

### Analysis of hourly traffic
1. Average (median and mean) games per hour
2. Distribution of games per hour
3. Review of hours where game count is 0
3. Average (mean) games per hour by day of week
4. Average (mean) games per hour by hour of day
5. Average (mean) games per hour by hour of week
6. Average (mean) games per hour by day of month
7. Average (mean) games per hour by month of year
8. Average (mean) games per hour by day of year
9. Traffic trends beyond the scope of this data set


### Analysis of player activity (returns and game count)
1. Count of unique players
2. Average (mean) roi by games played (scatter)
3. Variance calculator (randomly generates cumulative profit for given win rate, sample size and associated profit/loss for game win/loss)
4. Average (mean) roi by games played (players grouped by game count)
5. Total profit against game count
6. Distribution of cumulative profit by player
7. Distribution of total game count by player

### Analysis of player subsets
Splitting players into two groups, those that play less than 400 games, 'the many' (99.5% of players), and those that play more than 400 games 'the few' (0.5% of players), perform further analysis:
1. Total profit and game count of 'the many' and 'the few'
1. 'The few': Total profit by player distribution, average (mean) roi by player distribution
2. 'The many': Total profit by player distribution, average (mean) roi by player distribution
3. 'The few vs the few: Construction and analysis of pairwise matrix showing game count between top 20 players (top 20 by profit and top 20 by volume - 25 players total).
4. Detailed analysis of losing player in pairwise matrix
6. Network graph (25 players total, same as above)
5. Analysis of hourly traffic of most frequent players
5. 'The many' vs 'the many': construction of function that, given list of players, returns % of total games that players played vs other players in the list (scale 0 to 1).
5. Analysis of traffic between player groups using the above function 

### Analysis of periods with highest game counts
1. Analysis of hours where number of games played exceeds 90.

### Conclusions
1. Summary
2. Next steps
3. Modelling considerations






In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(font_scale=1.5)
from datetime import datetime
from datetime import timedelta
import copy

# Standard plotly imports
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
from plotly import tools
import networkx as nx

# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

# this line tells jupyter notebook to put the plots in the notebook rather than saving them to file
%matplotlib inline

# this line makes plots prettier on mac retina screens - if you don't have one it shouldn't do anything
%config InlineBackend.figure_format = 'retina'

### Import data

In [2]:
ht=pd.read_csv('hourly_traffic.csv')
ps=pd.read_csv('Player_summary.csv')
ts=pd.read_csv('Tournament_summary.csv')

In [3]:
ps.head()

player_id  game_count  total_profit  avg_roi_%  avg_stake
0    Aaron Barnes           1            49      96.08       51.0
1  Aaron Bell Jr.           3           -53     -34.64       51.0
2  Aaron Castillo           2          -102    -100.00       51.0
3      Aaron Cruz           1           -51    -100.00       51.0
4      Aaron Diaz          23          -573     -48.85       51.0

In [4]:
ht.head()

date_time  game_count day_of_week
0  2015-11-04 16:00:00          20         wed
1  2015-11-04 17:00:00          15         wed
2  2015-11-04 18:00:00          14         wed
3  2015-11-04 19:00:00          27         wed
4  2015-11-04 20:00:00          36         wed

In [5]:
ts.head()

date_time  tournament_id  total_buyin  prize_buyin  rake_buyin  \
0  2015-11-04 16:00:01              1           51           50           1   
1  2015-11-04 16:07:49              2           51           50           1   
2  2015-11-04 16:12:36              3           51           50           1   
3  2015-11-04 16:21:04              4           51           50           1   
4  2015-11-04 16:21:54              5           51           50           1   

   first_place_id     second_place_id  first_place_prize  finishing_level  
0     Mark Hunter          Juan Avery                100                1  
1  Michelle Wiley          Dana Brown                100                1  
2      Dana Brown       Richard Myers                100                2  
3      Dana Brown       Mary Campbell                100                1  
4     Jesse Myers  Jonathon Hernandez                100                3

In [6]:
#recast date_time column as type date_time
ht['date_time']= ht['date_time'].apply(pd.Timestamp)
ts['date_time']= ts['date_time'].apply(pd.Timestamp)

#create hour of day column
ht['hour_of_day']=[i.hour for i in ht.date_time]

#create day of week as number column - for plotting multiple days in order
ht['num_day_of_week']=[i.weekday() for i in ht.date_time]

#create month column
ht['month']=[i.month for i in ht.date_time]

#create day of month column
ht['day_of_month']=[i.day for i in ht.date_time]

ts.set_index('date_time', inplace=True)
ht.set_index('date_time', inplace=True)


In [7]:
ps.head()

player_id  game_count  total_profit  avg_roi_%  avg_stake
0    Aaron Barnes           1            49      96.08       51.0
1  Aaron Bell Jr.           3           -53     -34.64       51.0
2  Aaron Castillo           2          -102    -100.00       51.0
3      Aaron Cruz           1           -51    -100.00       51.0
4      Aaron Diaz          23          -573     -48.85       51.0

In [8]:
ps.describe()

game_count  total_profit     avg_roi_%  avg_stake
count  14483.000000  14483.000000  14483.000000    14483.0
mean      27.620935    -27.620935    -21.017657       51.0
std      311.567004    763.060668     65.113450        0.0
min        1.000000  -7098.000000   -100.000000       51.0
25%        1.000000   -102.000000   -100.000000       51.0
50%        3.000000    -51.000000    -17.040000       51.0
75%        9.000000     47.000000     12.040000       51.0
max    18790.000000  34310.000000     96.080000       51.0

In [9]:
ht.head()

game_count day_of_week  hour_of_day  num_day_of_week  \
date_time                                                                   
2015-11-04 16:00:00          20         wed           16                2   
2015-11-04 17:00:00          15         wed           17                2   
2015-11-04 18:00:00          14         wed           18                2   
2015-11-04 19:00:00          27         wed           19                2   
2015-11-04 20:00:00          36         wed           20                2   

                     month  day_of_month  
date_time                                 
2015-11-04 16:00:00     11             4  
2015-11-04 17:00:00     11             4  
2015-11-04 18:00:00     11             4  
2015-11-04 19:00:00     11             4  
2015-11-04 20:00:00     11             4

In [10]:
ht['game_count'].describe()

count    7565.000000
mean       26.439788
std        16.495227
min         0.000000
25%        15.000000
50%        23.000000
75%        35.000000
max       139.000000
Name: game_count, dtype: float64

In [11]:
ts.finishing_level.describe()

count    200017.000000
mean          2.202758
std           1.133705
min           1.000000
25%           1.000000
50%           2.000000
75%           3.000000
max          17.000000
Name: finishing_level, dtype: float64

## Game traffic

### Average games per hour

In [12]:
ht.game_count.mean()

26.439788499669532

In [13]:
ht.game_count.median()

23.0

### Distribution of hourly game count

In [14]:
ht.game_count.iplot(kind='hist', xTitle='Games per hour',
                  yTitle='Frequency', title='Games per hour disribution')

The frequency 0 games per hour needs to be investigated as it clearly defies the expected trend, possible causes:
1. The poker site is temporarily closed for maintenance
3. The scraping of traffic has been interrupted due to technical issues
3. Nobody is playing

With only 73 instances we can manually inspect the instances of no traffic.

In [15]:
ht[ht.game_count==0]

game_count day_of_week  hour_of_day  num_day_of_week  \
date_time                                                                   
2015-11-25 11:00:00           0         wed           11                2   
2015-12-13 19:00:00           0         sun           19                6   
2015-12-21 12:00:00           0         mon           12                0   
2015-12-21 13:00:00           0         mon           13                0   
2015-12-21 16:00:00           0         mon           16                0   
2015-12-21 17:00:00           0         mon           17                0   
2015-12-21 18:00:00           0         mon           18                0   
2015-12-21 19:00:00           0         mon           19                0   
2015-12-21 20:00:00           0         mon           20                0   
2015-12-21 22:00:00           0         mon           22                0   
2015-12-21 23:00:00           0         mon           23                0   
2015-12-22 00:00:00           0         tue            0                1   
2015-12-22 01:00:00           0         tue            1                1   
2015-12-22 02:00:00           0         tue            2                1   
2015-12-22 03:00:00           0         tue            3                1   
2015-12-22 04:00:00           0         tue            4                1   
2015-12-31 11:00:00           0        thur           11                3   
2016-01-15 20:00:00           0         fri           20                4   
2016-01-24 17:00:00           0         sun           17                6   
2016-02-03 11:00:00           0         wed           11                2   
2016-02-21 19:00:00           0         sun           19                6   
2016-03-03 22:00:00           0        thur           22                3   
2016-03-10 11:00:00           0        thur           11                3   
2016-04-14 11:00:00           0        thur           11                3   
2016-04-24 16:00:00           0         sun           16                6   
2016-04-24 17:00:00           0         sun           17                6   
2016-04-24 19:00:00           0         sun           19                6   
2016-05-01 17:00:00           0         sun           17                6   
2016-05-01 20:00:00           0         sun           20                6   
2016-05-09 00:00:00           0         mon            0                0   
...                         ...         ...          ...              ...   
2016-06-12 21:00:00           0         sun           21                6   
2016-06-19 16:00:00           0         sun           16                6   
2016-06-19 17:00:00           0         sun           17                6   
2016-06-19 18:00:00           0         sun           18                6   
2016-06-25 18:00:00           0         sat           18                5   
2016-06-26 19:00:00           0         sun           19                6   
2016-07-03 17:00:00           0         sun           17                6   
2016-07-03 19:00:00           0         sun           19                6   
2016-07-13 11:00:00           0         wed           11                2   
2016-07-17 06:00:00           0         sun            6                6   
2016-07-17 18:00:00           0         sun           18                6   
2016-07-17 21:00:00           0         sun           21                6   
2016-07-24 19:00:00           0         sun           19                6   
2016-07-31 17:00:00           0         sun           17                6   
2016-07-31 18:00:00           0         sun           18                6   
2016-07-31 19:00:00           0         sun           19                6   
2016-07-31 20:00:00           0         sun           20                6   
2016-08-04 15:00:00           0        thur           15                3   
2016-08-04 16:00:00           0        thur           16                3   
2016-08-04 17:00:

We do not consider 0 games an hour impossible, so the best approach here will involve filling in a portion of these values that are expected to be a result of issues of issues 1 and 2 described above.

Many of these instances of 0 game counts are in sequential hours. Given 0 hour games happen approximately 1% of the time in our sample, it is unlikely that so many instances of sequential 0 game hours would be witnessed (these instances will be filled). 



### Average traffic by day

In [16]:
#group by day
weekly_avg=ht.groupby('day_of_week').mean()['game_count'].loc[["mon", "tue", "wed","thur","fri","sat","sun"]]

In [17]:
weekly_avg.iplot(kind='bar', 
                 xTitle='Day', 
                 yTitle='Games per hour', 
                 title='Average games per hour by day', 
                 yrange=[20,30])

Unexpectedly, weekends are not the days with the highest traffic (for this particular variant and stake of poker!).

### Average traffic by hour of day

In [18]:
daily_avg=ht.groupby('hour_of_day').mean()['game_count']

In [25]:
daily_avg.iplot(kind='bar',
                xTitle='Hour of day', 
                yTitle='Games per hour',
                title='Average games per hour by hour of day')

There are restrictions on which countries poker websites are allowed to operate in. Reasons for restrictions on poker websites operating in markets (countries) are varied, they include:
1. An outright ban on online gambling, or uncertainty regarding its legal status (Qatar, Poland, Malaysia)
2. A requirement for licenses, sometimes difficult to obtain (United States)
3. Laws requiring domestic player pools to be fenced off from the rest of the world (France, Italy)

Excluding the United States, it is often Western and European countries that have the most liberal online gambling laws. Countries who's time zones are within 3 hours either side of Greenwich Mean Time make up the majority of traffic to global poker websites. The average games per hour of day indicate that the timezone represented by these times are likely within 2 hours of GMT.

For further information on global population by timezone see https://blog.cyberclip.com/world-population-by-time-zone

In [20]:
#To make differencing valid for every hour copy 23:00-00:00 and place before 00:00 to 01:00

#copy daily average
daily_avg_diff=copy.copy(daily_avg)

#add 1 to every index
daily_avg_diff.index=[i+1 for i in daily_avg_diff.index]

#insert final value in table as first value of table
daily_avg_diff[0]=daily_avg_diff[24]

#take difference, drop nan, reset index
daily_avg_diff=daily_avg_diff.sort_index().diff().dropna().reset_index(drop=True)

In [21]:
daily_avg_diff.iplot(kind='bar',
                 xTitle='Hour of day', 
                 yTitle='Games per hour (differenced)',
                 title='Average games per hour by hour of day (differenced)')

The difference in average games per hour (between sequential hours) shows that there are distinct sections of the day where traffic increases and decreases. 

### Average traffic by hour of week

In [21]:
#0=monday, 1=tuesday... 6=sunday
#time of week display in (day, hour) 
ht.groupby(['num_day_of_week', 'hour_of_day'])['game_count'].mean()\
.iplot(kind='line',
       xTitle='(Day, Hour)',
       yTitle='Games per hour',
       title='Average games per hour by hour of week')

This shows that each day of the week broadly reflects the trend as shown in the average games per hour by hour of day bar chart. There are however some distinct difference between days, particularly Sunday where traffic is notably lower, and Friday and Thursday evening, which see the highest levels of traffic. 

Adding a weekly seasonal component to the time series model is likely to improve the forecast.

### Average traffic by day of month

In [23]:
ht.groupby('day_of_month').mean()['game_count'].iplot(kind='bar', 
                 xTitle='Day of month', 
                 yTitle='Average Games per hour', 
                 title='Average games per hour by day of month', 
                 )

There is no identifiable tendency of higher volume during certain times of the month.

Interestingly, the 13th of the month is the day with the highest traffic


In [26]:
ht.resample('D')['game_count'].mean()\
.iplot(kind='line',
       xTitle='Day',
       yTitle='Average Games per hour',
       title='Average games per hour by day of year')

The weekly trend is significantly more pronounced than any monthly trend, it is unlikely adding a day of the month component to our model will improve its forecasting accuracy. In any case, the time span covered by the data set is too small to justify doing so at the moment.

The increased traffic in December is short lived. It is possible this slight anomaly was caused by an external factor like a promotion for the particular game variant in our sample. 

## Trafic trends beyond the scope of this data set

It is common knowledge in the poker industry that the traffic for heads up variants of poker has decreased since their rise to popularity in late 2011. It's original popularity, driven by it's short game time and coin flip nature, has slowly diminished with time as new poker variants gain popularity, markets shrink and segment and more companies enter the market. 

Additionally, due to the symmetrical nature of heads up play, it is the easiest form of poker to 'solve'. Although the route to the optimal solution exists, the computational power required to derive it in it's full form exceeds the projected returns that may be had by having access to it (sites ban cheaters!). However, approximations of the optimal playing strategy are capable of beating the most experienced professionals and are now widely available. As these solutions become more accurate,  more available and easier to use it is possible that the formats popularity will decrease further.

## Player activity and results

In [25]:
#Number of unique players in the data set
ps.shape[0]

14483

## Returns on investment are bounded

In [26]:
trace = go.Scattergl(
    x = ps['game_count'],
    y = ps['avg_roi_%'],
    text= ps['player_id'],
    mode = 'markers',
    opacity= .6,
    marker = dict(color = '#FFBAD2',
                  line = dict(width = 1)))

layout=  go.Layout(title='avg roi(%) against game count',
                   xaxis=dict(type='log', autorange=True, title='Game count'),
                    yaxis=dict(title='avg roi (%)'))

data = [trace]
fig = go.Figure(data=data, layout=layout)

iplot(fig)

As game count increases, roi's are constrained to a narrower range. This reflects the increased likelihood that the average roi reflects a players true roi (as would be inferred by their skill level) as the total sample of games played increases.

Compared to other formats of poker, roi's converge in relatively short sample of games. This reflects the fact that heads up games are one of the lowest variance formats of poker - owing entirely to it being a game of two players. This would make it a popular format for winning professionals seeking a reliable income.

(Interestingly, the baseline strategy in poker involves going all in every hand. With this strategy a player would expect to win more than 25% of games over a significant sample. This approximates to a -50% roi, (and a 50% roi for the opponent) this common sense limitation on possible roi's over large samples is also reflected in the plot.

Reassuringly, there are no anomalies on roi's for players over 1000 games, it is unlikely anybody in this sample has been able to cheat and continue playing.

## The less you win, the less you play

In [27]:
#copy player summary
ps_grouped_roi=copy.copy(ps)

#group by game count, take mean roi and count
ps_grouped_roi=ps_grouped_roi.groupby('game_count').agg({'avg_roi_%':['mean', 'count']})

In [28]:
#calculate line of best fit
#points are weighted by number of games represented 
#by grouped players total game count
x=[]
y=[]
for i in ps_grouped_roi.index:
    for j in range(int(ps_grouped_roi.loc[i][1])):
        for k in range(i):
            x.append((np.log(i)))
            y.append(ps_grouped_roi.loc[i][0])

z=np.polyfit((x), (y), 2)

x1=[]
y1=[]
for i in range(1, 18800):
    x1.append(i)
    y1.append(((z[0]*np.log(i)**2)+(z[1]*np.log((i)))+z[2]))

In [29]:
trace1 = go.Scattergl(
    name='Grouped players',
    x = ps_grouped_roi.index,
    y = ps_grouped_roi['avg_roi_%']['mean'],
    #hover over value to see sample size it was based on
    text=ps_grouped_roi['avg_roi_%']['count'],
    mode = 'markers',
    marker = dict(color = np.log(ps_grouped_roi['avg_roi_%']['count']),
                  line = dict(width = 1)))

trace2 = go.Scatter(x = x1, y = y1, name= 'Weighted best fit')


layout=  go.Layout(title='avg roi(%) against game count',
                   xaxis=dict(type='log', autorange=True, title='Game count'),
                    yaxis=dict(title='avg roi (%)'),
                  legend=dict(x=0,y=1,
                              traceorder='normal',
                              font=dict(size=10),
                               bordercolor='#FFFFFF'))

data = [trace1, trace2]
fig = go.Figure(data=data, layout=layout)

iplot(fig)



For this plot players have been grouped by number of games played to give the mean of the mean roi's. Because grouping is done on individual game counts (not custom bins of varying length) the centre of the graph is quite noisy. The line of best fit is weighted to the number of games in each grouping. The colour density is represents log of the number of players in the group.

Here we have a best guess of a players roi based on their game count. As expected, average win rates are higher for players who play more games. This demonstrates a players ability to keep playing based on their return on investment, those with negative return on investments rarely continue beyond 1000 games.

Although we can make the soft assumption that the more one plays the better they would expect to be, there is no evidence that more experience gives any guarantee of a positive roi. 

### A relibale income is for the limited few

In [30]:
trace = go.Scattergl(
    x = ps['game_count'],
    y = ps['total_profit'],
    text= ps['player_id'],
    mode = 'markers', 
    opacity= 1,
    marker = dict(color = '#FFBAD2',
                  line = dict(width = 1)))

layout=  go.Layout(title='Total profit against game count',
                 xaxis=dict(type='log',autorange=True, title='Game count'),
                    yaxis=dict(title='total profit $'))

data = [trace]
fig = go.Figure(data=data, layout=layout)

iplot(fig)

### Total profit by player distribution

In [31]:
ps.total_profit.iplot(kind='hist', 
                      xTitle='Total profit',
                      yTitle='Count', 
                      title='Total profit by player distribution', 
                      bins=100, 
                      logy=True)

Here we see that a majority of players experience a nominal win/loss over their entire player sample. Approximately 13000 players win/lose less than 500. Again we see losers give up sooner that winners, which  is reflected in the density of the distribution either side of 0 (denser below 0,  with a more sporadic distribution above 0).



### Total games by player distribution 

In [32]:
ps.game_count.iplot(kind='hist',
                    xTitle='Total games played',
                    yTitle='Count', 
                    title='Total games played distribution', 
                    bins=100, 
                    logy=True,
                     )

Approximately 99% of players have played less than 200 games over a year sample. Of the remaining 1%, half fall into the 200-400 games played bin, and the final half falls into a 400-19000 games played bin.

We saw in our previous plots that players with less than 400 games are predominantly losing players. 

Here we begin to see the emergence of two classes of players, the majority, over 99%, are casual players with varying win rates, and a small minority, less than 1%, play more often and see sizable returns in their sample. Broadly, we can consider the majority (>99%) recreational/novice players and a small minority (<1%) professional/winning players.

Given the sample size of some of the more frequent players (and the fact that professional poker players generally stick to a few games types they perform best in), it would be a safe assumption to say any player considering themselves a professional would have a sample size greater than 400 games within a given year.

## 99.5% vs .5%

In [29]:
#The combined profit and game count with players under 400 games
print(ps[ps.game_count<400].shape[0], 'players under 400 games')
print(ps[ps.game_count<400][['total_profit','game_count']].sum())
print('\n')

#The combined profit and game count with players over 400 games
print(ps[ps.game_count>=400].shape[0], 'players over 400 games')
print(ps[ps.game_count>=400][['total_profit','game_count']].sum())
print('\n')

#hosts profit!
print('1 poker provider, total profit: $' ,round(ts.rake_buyin.sum(),2))

14394 players under 400 games
total_profit   -800398
game_count      167998
dtype: int64


89 players over 400 games
total_profit    400364
game_count      232036
dtype: int64


1 poker provider, total profit: $ 200017


By comparing the distibution of roi's for players that play above and below 400 games (the 0.5% and the 99%) we can further evaluate the validity of our classification of recreational players and winning professionals. 

In [34]:
ps_over4=ps[ps.game_count>=400][['total_profit','avg_roi_%']]
ps_over4.columns=['Total profit', 'Average roi %']

ps_over4.iplot(kind='hist', 
       #   xTitle='Average roi',
          yTitle='Count', 
          title='Profit and roi distribution (players over 400 games)', 
          bins=20, 
          logy=False, 
          subplots=True)

We see a much higher portion of winners in this sample. There are still losers in the sample, but by comparing the histograms we can see that those with the lowest roi's didn't play for too long (as no player lost more than 10000). We can improve the our accuracy on classifying recreational and professional players by increasing the threshold above 400 games and incorporating a profit variable.

In [35]:
ps_under4=ps[ps.game_count<400][['total_profit','avg_roi_%']]
ps_under4.columns=['Total profit', 'Average roi %']

ps_under4.iplot(kind='hist', 
       #   xTitle='Average roi',
          yTitle='Count', 
          title='Profit and roi distribution (players under 400 games)', 
          bins=20, 
          logy=True, 
          subplots=True)

With less than 400 games in their sample very few of these players win/lose a significant amount, and their roi's vary significantly. This distribution is evidence that it is difficult to accuratley categeroise a players skill level with a sample size less than 400 games (we would perform better taking our line of best fit from the avg roi vs game count plot as an estimation).

## Variance calculator

In [36]:
def variance_calculator(winrate, win_profit, loss_profit, sample):
    """Takes win rate (as % with two decimal places), profit associates with win (prize-buyin),
    loss associates with lose (tournament buyin) and sample size.
    
    Generates randomly generated results given win rate for sample size"""
    win=winrate*100
    sample_results=np.random.randint(0,10000, sample)
    results = sample_results<win
    results=[win_profit if i==True else loss_profit for i in results]
    results=[0]+results
    cum_results= np.cumsum(results)
    
    
    expected_returns= (((win_profit-loss_profit)*(winrate/100))+loss_profit)*sample
    expected_roi=  expected_returns /((-1*loss_profit*sample))*100
    
    
    roi= (cum_results[-1]) /(-1*loss_profit*sample)*100
    
    print('Expected roi given win rate:', round(expected_roi,2) ,'%')
    print('Expected profit given win rate: $', round(expected_returns,2))
    
    print('\n')
    
    print('Roi for randomly generated sample: ', round(roi,2), '%')
    print('Profit for randomly generated sample: $', round(cum_results[-1],2))
    
    cum_results=pd.DataFrame(cum_results, columns=['cumulative profit'])
    
    
    
    
    return cum_results.iplot(mode='lines', 
                            xTitle='Number of games', 
                            yTitle='Cumulative profit',
                            title='Cumulative profit',
                             layout=dict(xaxis=dict( title='Number of games', tickangle=45),
                                         yaxis=dict(title='Cumulative profit'),
                                         title='Randomly genereated cumulative profit given {}% win rate'.format(winrate)))


In [37]:
#caulcate possible outcomes given prizes in sample and 50% win rate
variance_calculator(53, 49, -51, 1000)

Expected roi given win rate: 3.92 %
Expected profit given win rate: $ 2000.0


Roi for randomly generated sample:  9.02 %
Profit for randomly generated sample: $ 4600


Running this function multiple times for a fixed winrate demonstrates the variance in cumulative profit for different win rates over a given game sample. 

From this we can see players with a greater than 50% winrate often experience cumulative losses over a 1000 game sample. Given this information, we should be cautious about classifying a players skill level based on their winrate over smaller samples.

## The few vs the few?

There are a handful of players that play a high volume of games in the sample size. We may be able to infer more about these players and contributers of traffic by looking at the relationships between them.

In [38]:
#returns dataframe showing game count between all unique players in list
#player with itself shows players total game count 
def versus_many(player_list, ts=ts, ps=ps):
    """takes list of players in form of list of strings
       returns dataframe showing gamecount between players all players
       player against self shows total game count, total profit
        """
    
    unique_players= np.unique(player_list)
    valid_players=[]
    for player in unique_players:
        if player in list(ps.player_id):
            valid_players.append(player)
        else:
            print(player, 'is not valid player id')
    
    player_dict={player: [0]*len(valid_players) for player in valid_players}
    
    versus_df=pd.DataFrame(player_dict, index=valid_players)
    
    for i in valid_players:
        for j in valid_players:
            if i==j:
                versus_df.loc[i,j]=str(int(ps[ps.player_id==i]['game_count']))+', $'+\
                str(int(ps[ps.player_id==i]['total_profit']))+', '+\
                str(float(ps[ps.player_id==i]['avg_roi_%']))+'%'
            else:
                info=ts[(ts.first_place_id==i) | (ts.second_place_id ==i)]
                info=info[(info.first_place_id==j) | (info.second_place_id ==j)]
                versus_df.loc[i,j]=len(info)
    
    return versus_df

In [39]:
#top 20 players by games played
top_20_volume=list(ps.sort_values(by='game_count', ascending=False).head(20).player_id)

#top 20 players by profit won
top_20_profit=list(ps.sort_values(by='total_profit', ascending=False).head(20).player_id)

top=list(pd.unique(top_20_profit+top_20_volume))

#set display options to view whole dataframe
pd.options.display.max_columns = 40

In [40]:
pairwise_games=versus_many(top)

In [41]:
pairwise_games

Angela Welch            Ashley Le  \
Angela Welch       2752, $11848, 8.44%                    0   
Ashley Le                            0  6548, $21852, 6.54%   
Bernard Baker                        0                    0   
Carl Maxwell                         0                    1   
Carrie Barnes                        1                    2   
Christopher Vance                    1                    1   
Cody Lopez                           0                    0   
Courtney Meyer                       0                    0   
Dana Brown                           0                    0   
Daniel Garrett                       0                    0   
Diana Hunter                         1                    0   
John Fischer                         0                    0   
Krystal Mendoza                      0                    0   
Louis Walker                         1                    1   
Manuel Clark                         0                    0   
Mark Strickland                      1                    0   
Melissa Matthews                     3                    3   
Michelle Goodman                     1                    2   
Nicholas Mueller                     0                    2   
Nicolas Martin                       1                    1   
Rebecca Campbell                     1                    0   
Robin Jones                          0                    0   
Sean Foster II                       2                  105   
Susan Graham                         0                    0   
Wayne Leach II                       1                    4   

                         Bernard Baker        Carl Maxwell  \
Angela Welch                         0                   0   
Ashley Le                            0                   1   
Bernard Baker      5696, $22204, 7.64%                   1   
Carl Maxwell                         1  7126, $7474, 2.06%   
Carrie Barnes                        3                   2   
Christopher Vance                    0                   1   
Cody Lopez                           1                   0   
Courtney Meyer                       0                   0   
Dana Brown                           0                   0   
Daniel Garrett                       0                   0   
Diana Hunter                         1                   0   
John Fischer                         0                   0   
Krystal Mendoza                      0                   0   
Louis Walker                         3                   2   
Manuel Clark                         0                   0   
Mark Strickland                      0                   0   
Melissa Matthews                     2                   0   
Michelle Goodman                     2                   0   
Nicholas Mueller                     1                  25   
Nicolas Martin                       0                   1   
Rebecca Campbell                     0                   1   
Robin Jones                          0                   1   
Sean Foster II                      56                 910   
Susan Graham                         1                   0   
Wayne Leach II                       1                   2   

                          Carrie Barnes    Christopher Vance  \
Angela Welch                          1                    1   
Ashley Le                             2                    1   
Bernard Baker                         3                    0   
Carl Maxwell                          2                    1   
Carrie Barnes      18790, $34310, 3.58%                    3   
Christopher Vance                     3  4256, $14944, 6.88%   
Cody Lopez                            5                    0   
Courtney Meyer                        0                    0   
Dana Brown                            2                    0   
Daniel Garrett                        0                    0   
Diana Hunter                         61                    0   
John F

25 players are in this dataframe, showing a high overlap between the top 20 players by profit and top 20 by volume.

All players in the dataframe have game counts above 2000. Despite this they all play almost no games with each other. Such small game counts between the most frequent players, who are all (but one) winners,  demonstrates that some winning players make an active effort to avoid playing with each other. 

We see in the sample there is one player who plays a large number of games against the other professionals, despite such strong opponents their roi is not much lower than the sunk cost (rake) associated with each game. This player is likely a better than average player who experiences low returns because they play most of their games against other professionals. 

In [42]:
#set diagonal values to 0
pairwise_games=pairwise_games.applymap(lambda x: 0 if type(x)==str else x)

In [43]:
#order players by game_count against other players in group
most=pd.DataFrame(pairwise_games.sum().sort_values(ascending=False), columns=['count'])

In [44]:
#take most frequent player (only losing player in sample)
freq_player=most.index[0]

In [45]:
#take loser column,  remove identity element and make into dataframe
loser=pd.DataFrame(pairwise_games[pairwise_games.index != freq_player][freq_player])

#make copy of player summary with player as index
ps_id=ps.set_index('player_id')

#subset player summary copy by top 20 profit/volume players (excluding loser)
index_by=copy.copy(top)
index_by.remove(freq_player)
joining=ps_id.loc[index_by].sort_values(by='avg_roi_%', ascending=False)

#merge dataframes
merged_df=pd.merge(loser, joining, left_index=True, right_index=True)

#take games vs loser and avg roi of player (all games)
megred_df=merged_df[[freq_player, 'avg_roi_%']]

In [46]:
#percent of losing players games played vs top 20 volume/profit players
merged_df[freq_player].sum()/ps_id.loc[freq_player]['game_count']

0.8968514266972778

In [47]:
merged_df.sort_values('avg_roi_%', ascending=False)

Sean Foster II  game_count  total_profit  avg_roi_%  \
Daniel Garrett                  1        3168         16132       9.98   
Wayne Leach II                 16        2350         10850       9.05   
Angela Welch                    2        2752         11848       8.44   
Dana Brown                      0        4956         19644       7.77   
Bernard Baker                  56        5696         22204       7.64   
John Fischer                    0        3884         15116       7.63   
Courtney Meyer                 26        4359         16391       7.37   
Rebecca Campbell                3        3153         11497       7.15   
Christopher Vance               0        4256         14944       6.88   
Ashley Le                     105        6548         21852       6.54   
Susan Graham                  108        8114         25486       6.16   
Nicholas Mueller                3       10037         27613       5.39   
Cody Lopez                    122        6602         17498       5.20   
Manuel Clark                    0        6095         15755       5.07   
Krystal Mendoza               442        6773         17277       5.00   
Diana Hunter                   50        5696         12604       4.34   
Michelle Goodman              205        6012         13188       4.30   
Louis Walker                  157        4356          9544       4.30   
Carrie Barnes                 442       18790         34310       3.58   
Melissa Matthews              264        6785         11265       3.26   
Mark Strickland              1836       12243         17907       2.87   
Robin Jones                   490        4394          5406       2.41   
Carl Maxwell                  910        7126          7474       2.06   
Nicolas Martin                231        7021          1729       0.48   

                   avg_stake  
Daniel Garrett          51.0  
Wayne Leach II          51.0  
Angela Welch            51.0  
Dana Brown              51.0  
Bernard Baker           51.0  
John Fischer            51.0  
Courtney Meyer          51.0  
Rebecca Campbell        51.0  
Christopher Vance       51.0  
Ashley Le               51.0  
Susan Graham            51.0  
Nicholas Mueller        51.0  
Cody Lopez              51.0  
Manuel Clark            51.0  
Krystal Mendoza         51.0  
Diana Hunter            51.0  
Michelle Goodman        51.0  
Louis Walker            51.0  
Carrie Barnes           51.0  
Melissa Matthews        51.0  
Mark Strickland         51.0  
Robin Jones             51.0  
Carl Maxwell            51.0  
Nicolas Martin          51.0

The first column (Sean Foster II) represents the number of games played against this player, the other columns are the players global statistics.

Here we see that the losing players (Sean Foster II) prefers to play the weaker players in this list. Given the consistency with which stronger players are avoided we assume either the player is intentionally targeting players with a lower roi (higher roi indicates higher skill level) or is impacting the players roi's by playing them so much.

Given that in many instances games vs Sean Foster II represent a small portion of the players global games, we consider the former (Sean Foster II is intentionally targeting them) the more likely scenario.

### Pairwise relationship top 25 players

In [48]:
#get positions of nodes
G=nx.Graph(pairwise_games)
pos = nx.drawing.spring_layout(G)

#NOTE: improve edge trace by layering multiple edge traces (partitioned by game count), such that
#line strength also represents game count - use code below to mask dataframes for diff traces
#used to put filer on pairwise matrix
#where_are_NaNs = np.isnan(top_df[top_df>10])
#top_df[where_are_NaNs] = 0

#initiate empty edge trace
edge_trace = go.Scatter(
    x=[],
    y=[],
    line=dict(width=0.5,color='#888'),
    hoverinfo='none',
    mode='lines')

#populate edge trace using  node positions
for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_trace['x'] += tuple([x0, x1, None])
    edge_trace['y'] += tuple([y0, y1, None])


#initiate empty node trace
node_trace = go.Scatter(
    x=[],
    y=[],
    text=[],
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=False,#toggle to show colour bar
        # colorscale options
        #'Greys' | 'YlGnBu' | 'Greens' | 'YlOrRd' | 'Bluered' | 'RdBu' |
        #'Reds' | 'Blues' | 'Picnic' | 'Rainbow' | 'Portland' | 'Jet' |
        #'Hot' | 'Blackbody' | 'Earth' | 'Electric' | 'Viridis' |
        colorscale='Bluered',
        reversescale=True,
        color=[],
        size=10,
#         colorbar=dict(
#             thickness=15,
#             title='Node Connections',
#             xanchor='left',
#             titleside='right'
#         ),
        line=dict(width=2)))

#populate node trace with node positions
for node in G.nodes():
    x, y = pos[node]
    node_trace['x'] += tuple([x])
    node_trace['y'] += tuple([y])
    

#set node size equal to absolute average roi
node_trace['marker']['size']=list(np.absolute(ps_id.loc[list(G.nodes)]['avg_roi_%'])*7)

#set colour by whether average roi is positive or negative (blue=profit, red=loss)
node_trace['marker']['color']=(ps_id.loc[list(G.nodes)]['avg_roi_%']>0)*1 #profit/loss colour

#set hover text of node to be name of player
node_trace['text']=list(G.nodes)


#plot masterpiece
fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                title='Top players: network graph',
                titlefont=dict(size=16),
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20,l=5,r=5,t=40),
#                 annotations=[ dict(
#                     text="Python code: <a href='https://plot.ly/ipython-notebooks/network-graphs/'> https://plot.ly/ipython-notebooks/network-graphs/</a>",
#                     showarrow=False,
#                    xref="paper", yref="paper",
#                     x=0.005, y=-0.002 ) ],
                 xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

iplot(fig)

Colour of circle; blue=profit, red=loss
Size of circle; Average roi (red if negative)
Distance between circles; closer the more they play

Two things are noteworthy here, that the losing player plays most (almost 90%) of their games against the players with the highest profit or volume. And they seem to make an effort to avoid the players with the highest average roi's. 

Here we see a story emerging...

Professional players make an active effort to avoid playing each other. This probably arose as a result of playing each other at some point in the past (at a time before the earliest game in the sample we are studying). To enter the fold of professionals, players must prove themselves by playing existing professionals - to improve their chances of success they focus their efforts on the weaker existing professionals. 

The original remit of this project is to provide information that increases a players expected profitability. If this component of player traffic, professionals vs aspiring professionals, yields no profit for the average established professional, we can consider removing these instances from the hourly traffic sample before forecasting traffic. In this way we are forecasting the traffic that professional players are interested in - games that involve recreational players only. 

In [49]:
#Function for all players vs specific player summary and it's dependencies

def get_avg_roi(player_id, ts=ts):
    #calculate roi for each individual game and take average
    #combine with average stake and game count to give most accurate
    #representation of skill level
    info=ts[(ts.first_place_id==player_id) | (ts.second_place_id ==player_id)]
    roi=(((info.first_place_id==player_id)*info.first_place_prize)/info.total_buyin).mean()
    return round((roi-1)*100,2)

def get_total_profit(player_id, ts=ts):
    info=ts[(ts.first_place_id==player_id) | (ts.second_place_id ==player_id)]
    return round(sum((info.first_place_id==player_id)*info.first_place_prize)-sum(info.total_buyin),2)

def get_game_count(player_id, ts=ts):
    return sum((player_id ==ts.first_place_id)*1)+sum((player_id==ts.second_place_id)*1)

def get_avg_stake(player_id, ts=ts):
    return round(ts[(ts.first_place_id==player_id) | (ts.second_place_id ==player_id)].total_buyin.mean(),2)

#could make this function faster by removing some columns 
#speed only an issue when players number of games exceeds 500

def versus_one(player_id, ts=ts):
    #filter all games including player_id and collect unique opponents
    info=ts[(ts.first_place_id==player_id) | (ts.second_place_id ==player_id)]
    players=list(np.unique((list(info.first_place_id)+list(info.second_place_id))))
    players.remove(player_id)
    
    #populate dataframe with info from filtered player list
    versus_df=pd.DataFrame(players, columns=['player_id'])
    versus_df['game_count']= versus_df.player_id.apply(lambda x: get_game_count(x, info))
    versus_df['player_total_profit']=versus_df.player_id.apply(lambda x: get_total_profit(x, info))
    versus_df['player_avg_roi_%']=versus_df.player_id.apply(lambda x: get_avg_roi(x, info))
    
    versus_df[(player_id+'_profit')]=versus_df.player_id.apply(lambda x:
                                        get_total_profit(player_id, info[(info.first_place_id==x) |
                                                                        (info.second_place_id==x)]))
    versus_df[(player_id+'_avg_roi_%')]=versus_df.player_id.apply(lambda x:
                                            get_avg_roi(player_id, info[(info.first_place_id==x) |
                                                                        (info.second_place_id==x)]))
    
    versus_df['avg_stake']=versus_df.player_id.apply(lambda x: get_avg_stake(x, info))

    return versus_df.set_index('player_id')

In [50]:
versus_loser=versus_one(freq_player)

In [51]:
versus_loser.reindex(top).dropna().sort_values('game_count', ascending=False)

game_count  player_total_profit  player_avg_roi_%  \
player_id                                                             
Mark Strickland       1836.0              -4736.0             -5.06   
Carl Maxwell           910.0                790.0              1.70   
Robin Jones            490.0              -1590.0             -6.36   
Carrie Barnes          442.0               -142.0             -0.63   
Krystal Mendoza        442.0                258.0              1.14   
Melissa Matthews       264.0               -964.0             -7.16   
Nicolas Martin         231.0                319.0              2.71   
Michelle Goodman       205.0               -155.0             -1.48   
Louis Walker           157.0                993.0             12.40   
Cody Lopez             122.0                178.0              2.86   
Susan Graham           108.0                192.0              3.49   
Ashley Le              105.0                645.0             12.04   
Bernard Baker           56.0                344.0             12.04   
Diana Hunter            50.0               -350.0            -13.73   
Courtney Meyer          26.0                174.0             13.12   
Wayne Leach II          16.0                284.0             34.80   
Nicholas Mueller         3.0                147.0             96.08   
Rebecca Campbell         3.0               -153.0           -100.00   
Angela Welch             2.0                 -2.0             -1.96   
Daniel Garrett           1.0                -51.0           -100.00   

                  Sean Foster II_profit  Sean Foster II_avg_roi_%  avg_stake  
player_id                                                                     
Mark Strickland                  1064.0                      1.14       51.0  
Carl Maxwell                    -2610.0                     -5.62       51.0  
Robin Jones                       610.0                      2.44       51.0  
Carrie Barnes                    -742.0                     -3.29       51.0  
Krystal Mendoza                 -1142.0                     -5.07       51.0  
Melissa Matthews                  436.0                      3.24       51.0  
Nicolas Martin                   -781.0                     -6.63       51.0  
Michelle Goodman                 -255.0                     -2.44       51.0  
Louis Walker                    -1307.0                    -16.32       51.0  
Cody Lopez                       -422.0                     -6.78       51.0  
Susan Graham                     -408.0                     -7.41       51.0  
Ashley Le                        -855.0                    -15.97       51.0  
Bernard Baker                    -456.0                    -15.97       51.0  
Diana Hunter                      250.0                      9.80       51.0  
Courtney Meyer                   -226.0                    -17.04       51.0  
Wayne Leach II                   -316.0                    -38.73       51.0  
Nicholas Mueller                 -153.0                   -100.00       51.0  
Rebecca Campbell                  147.0                     96.08       51.0  
Angela Welch                       -2.0                     -1.96       51.0  
Daniel Garrett                     49.0                     96.08       51.0

For players that the losing player has a sizeable sample versus, there is an even distibution of winners and losers among existing professionals. Also the existing professionals roi vs this player is generally lower than their average roi against the entire poker playing population. 

While professionals may have different opinions on what opponents they welcome, these results show that this player generally has a negative overall impact on another professionals total profit such that the games vs them  could be considered unwelcome. 

And why would professional keep playing in circumstances where there is clearly little value in doing so? Here we see the pressure associated with being a professional when facing new aspiring professionals; showing weakness could result in a breakdown of the agreement between other existing professionals (to not play each other). The choice becomes play a handful of new players, or see more experienced players turn on you.


### Mean games per hour for time online - top pros

In [52]:
ts.dtypes

tournament_id         int64
total_buyin           int64
prize_buyin           int64
rake_buyin            int64
first_place_id       object
second_place_id      object
first_place_prize     int64
finishing_level       int64
dtype: object

In [53]:
def get_player_hourly_traffic(player_id, ts=ts):
        
    #all games including player_id
    info=ts[(ts.first_place_id==player_id) | (ts.second_place_id ==player_id)]
    
    #resample by hour, name column 'count'
    df=pd.DataFrame(info.first_place_id.resample('H').count())
    df=df.rename(columns={"first_place_id": "game_count"})
    
    return df

In [54]:
#Hourly traffic of player attempting to enter group of professionals
per_hour=get_player_hourly_traffic(freq_player)

In [55]:
#Mean games per hour given online
per_hour[per_hour.game_count>0].mean()

game_count    15.595908
dtype: float64

In [56]:
#collect identity of the highest volume players (all games) in data set
highest_vol_player=ps.sort_values(by='game_count', ascending=False)['player_id'].iloc[0]

highest_vol_player_2=ps.sort_values(by='game_count', ascending=False)['player_id'].iloc[1]

highest_vol_player_3=ps.sort_values(by='game_count', ascending=False)['player_id'].iloc[2]

In [57]:
per_hour=get_player_hourly_traffic(highest_vol_player)

In [58]:
per_hour[per_hour.game_count>0].mean()

game_count    8.763993
dtype: float64

In [59]:
per_hour=get_player_hourly_traffic(highest_vol_player_2)

In [60]:
per_hour[per_hour.game_count>0].mean()

game_count    8.134884
dtype: float64

In [61]:
per_hour=get_player_hourly_traffic(highest_vol_player_3)

In [62]:
per_hour[per_hour.game_count>0].mean()

game_count    9.026079
dtype: float64

Players attempting to enter the fold of professionals have a higher average game count per hour (for hours online) than their most frequent opponents. The high games per hour and concentration of games against weaker opponents indicate that high volume against a player attempting to become a professional is either unavoidable or purposefully arranged.

This could be an important metric in determining whether a player playing larger volume against profitable players is a frequently playing recreational player or professional trying to gain entry into a higher tier of players.

## The many vs the many

Creating a pairwise matrix would be less difficult due to it's size; approx 14,000^2. 

Instead we create a function that, given player list, returns the frequency (out of 1) of games played by those players against other players in the list. (We consider the game count in this instance double the actual game count - i.e. game count experienced by players).

That the result for all players in our sample is one, we can also infer the relationship between two sets of players (if both sets combine to make the entire playing population).

In [63]:
def vs_list(player_list, ts=ts, ps=ps):
    """Given player list, return frequency of games played vs other players in list 
    Expressed on scale 0 (do not play each other at all) to 1, all by all players
    are against other players in the list
    
    Funcion gives sum of game count from players pov, so sum of games player will be double the number of games
    hosted"""
    
    print(len(player_list), 'players')
    
    #total games player by all players in list
    total_game_count=ps[ps.player_id.isin(player_list)]['game_count'].sum()
    
    print('Total games played by players in list: ', total_game_count)
    
    #number of games between players in list
    between=ts[ts.first_place_id.isin(player_list) & ts.second_place_id.isin(player_list)].shape[0]
    
    print('Total games played between players in list', 2*between)
    
    return (2*between)/total_game_count

We saw from earlier analysis that greater than 400 games was too low a threshold to indicate a player as a possible professional. Given the variance in results for players with low samples (under 1000 games) we are unable to accurately classify these players skill level based on their average return on investment. For players that we can be certain are winning professionals, their game count is always higher than 1000.

Let's look at the relationship between the two groups (more than/less than 1000 games)

In [64]:
the_many=list(ps[ps.game_count<1000]['player_id'])

In [65]:
vs_list(the_many)

14433 players
Total games played by players in list:  192509
Total games played between players in list 19558


0.10159525009220348

Only 10% of games played by players with less than 1000 games are played against other players with less than 1000 games. This is surprising since this makes up over 99.5% 

In [66]:
the_few=list(ps[ps.game_count>=1000]['player_id'])

In [67]:
vs_list(the_few)

50 players
Total games played by players in list:  207525
Total games played between players in list 34574


0.16660161426334177

Only 17% of the games played by players in this group are played against players in this group, (almost a third of these games can be attributed to the losing professional we identified above).

This mean that approximately 70-75% of games are played between the top 50 players and the bottom 14,400 players. 

Now we have an even clearer picture; a group of (likely) professionals take in turns playing against recreational players, (with a small number of games played within these defined groups)

In [28]:
#The combined profit and game count with players under 400 games
print(ps[ps.game_count<1000].shape[0], 'players under 400 games')
print(ps[ps.game_count<1000][['total_profit','game_count']].sum())
print('\n')

#The combined profit and game count with players over 400 games
print(ps[ps.game_count>=1000].shape[0], 'players over 400 games')
print(ps[ps.game_count>=1000][['total_profit','game_count']].sum())
print('\n')

#hosts profit!
print('1 poker provider, total profit: $' ,round(ts.rake_buyin.sum(),2))

14433 players under 400 games
total_profit   -832359
game_count      192509
dtype: int64


50 players over 400 games
total_profit    432325
game_count      207525
dtype: int64


1 poker provider, total profit: $ 200017


### A quick look at hours with the highest game counts

Browse the instances of high game counts to see whether there are variables in our data, or established trends that are contributing to this high volume of traffic.

In [68]:
ht[ht.game_count>90].reset_index(drop=True)

game_count day_of_week  hour_of_day  num_day_of_week  month  day_of_month
0           97         fri           21                4     11            13
1           91         wed           16                2     12             9
2          103         wed           19                2     12             9
3           97         wed           21                2     12             9
4          138        thur           17                3     12            10
5          114        thur           20                3     12            10
6          139        thur           21                3     12            10
7           91         fri           20                4     12            11
8          103         fri           21                4     12            11
9           95         fri           22                4     12            11
10          93         fri           23                4     12            11
11          97         sat            0                5     12            12
12          91         sat           16                5     12            12
13         122         sat           17                5     12            12
14          98         sat           23                5     12            12
15         107         sun           10                6     12            13
16         108         sun           15                6     12            13
17         120         sun           21                6     12            13
18          94         sun           22                6     12            13
19          91         sun           23                6     12            13
20         121         mon            9                0     12            14
21          91         mon           11                0     12            14
22          97         mon           15                0     12            14
23         130         mon           16                0     12            14
24          97         mon           17                0     12            14
25          98         wed           16                2     12            16
26         115        thur           20                3     12            17
27          96         fri           16                4     12            25
28          98         tue           21                1      1             5
29         115         tue           22                1      1             5
30         100         wed           22                2      1             6
31         110         wed           23                2      1             6
32         113         fri           23                4      1             8
33         113         sat            0                5      1             9
34         103         sat            1                5      1             9
35          97         wed           21                2      1            13
36         101         mon           21                0      1            18
37          91         mon           23                0      5             2
38          93         tue            0                1      5             3
39          91         fri           18                4      5            27
40          97        thur           10                3      8            25

Most of the instances of high traffic come during the period in December where there was a notable spike in traffic in the first half of the month. By filtering these hours we will see if there we can see if any particular players were responsible for this traffic.

In [69]:
#Hours with more tham 90 games
over_90_dec=ht[(ht.game_count>90)& (ht.month==12)]

over_90_dec.shape

(27, 6)

In [70]:
#subset the tournament summary data frame by the most popular hours.
dataframes=[]
for i in over_90_dec.index:
    start=i
    end=i+timedelta(hours=1)
    dataframes.append(ts[(ts.index>start) & (ts.index<end)])
        
popular_hours=pd.concat(dataframes)

In [71]:
popular_hours.shape

(2836, 8)

In [72]:
def player_summary_from_ts(df):
    "takes tournament summary dataframe an returns player summary dataframe"
    
    #Make data frame of all unique players
    player_df=pd.DataFrame(np.unique((list(df.first_place_id)+list(df.second_place_id))), columns=['player_id'])
    
    #build player results dataframe using helper functions
    player_df['game_count']= player_df.player_id.apply(lambda x: get_game_count(x, df))

    player_df['total_profit']= player_df.player_id.apply(lambda x: get_total_profit(x, df))

    player_df['avg_roi_%']= player_df.player_id.apply(lambda x: get_avg_roi(x, df))

    player_df['avg_stake']= player_df.player_id.apply(lambda x: get_avg_stake(x, df))
    
    return player_df

In [73]:
pop_hour_players=player_summary_from_ts(popular_hours)

In [74]:
pop_hour_players.shape

(410, 5)

In [75]:
pop_hour_players.sort_values('game_count', ascending=False).head(25)

player_id  game_count  total_profit  avg_roi_%  avg_stake
270         Mark Hunter         335         -1385      -8.11       51.0
73     Christopher Bush         246          -346      -2.76       51.0
54         Carl Maxwell         231           519       4.41       51.0
58            Chad Tran         190          -390      -4.02       51.0
240     Krystal Mendoza         185           465       4.93       51.0
312      Nicolas Martin         184         -1084     -11.55       51.0
285    Melissa Matthews         183           967      10.36       51.0
149    Jacqueline Green         179            71       0.78       51.0
295    Michelle Goodman         175          -125      -1.40       51.0
253  Leonard Villanueva         163           487       5.86       51.0
30            Ashley Le         162           138       1.67       51.0
115       Dustin Brooks         159         -1109     -13.68       51.0
7         Alyssa Huerta         157          -507      -6.33       51.0
158        Janet Brooks         139          -589      -8.31       51.0
48      Brooke Shepherd         139          -289      -4.08       51.0
204         Joshua Hall         122          -422      -6.78       51.0
305  Mrs. Jennifer Ford         120          -820     -13.40       51.0
77           Cody Lopez         120           880      14.38       51.0
32        Austin Parker         105           645      12.04       51.0
112       Donna Blevins         103           247       4.70       51.0
262        Louis Walker          88          -388      -8.65       51.0
18           Angel Pope          86           914      20.84       51.0
228      Kendra Jimenez          83          -633     -14.95       51.0
342         Robin Jones          80          -280      -6.86       51.0
356      Sean Foster II          80          -380      -9.31       51.0

Given the relatively small overlap between the players in this list and our previous top 20 volume players (for the entire sample), it is possible that an influx of recreational players during this period temporarily increased the traffic.

## Conclusions

In exploring the traffic and player tendencies we have gained a clearer picture of the seasonality of traffic and the skill level of varying players. In the context of our original objective, to provide professional poker players with new information that improves their win rate, two avenues present themselves worthy of following:

1. Providing summary information of players and player groups, made available with a search feature
2. Providing a time series model that forecasts poker traffic (in various forms)

Pursuing the summary information goal requires making an interface to search and display the information.

Pursuing the forecasting goal requires producing a time series model using the hourly traffic information. The EDA has shown the following factors should be considered when making a model:

1. There are both daily and weekly seasonal components to the traffic in the data set
1. Instances of sequential 0 games per hour should be filled (forward filled or average hour of week filled)
2. Players fall into two categories, casual/recreational players and professional players. An analysis of a players  roi, game count (total game count and mean game count for hours online) and most frequent opponents are useful for this classification.
3. Traffic that is professionals vs professionals is generally not a profitable prospect for the professionals involved due to the sunk cost associated with game (in the form of rake).
3. An unsupervised clustering algorithm or a supervised clustering algorithm (taking those easiest to identify as professionals or recreational players as the training set) could be used to classify players.
3. An accurate classification of professionals allows more detailed time series modelling that may provide more valuable information to professionals (modelling how many professionals are online in any hour and the traffic that includes at least one recreational player). 

 

